**LIBRARIES**

In [ ]:
import os
import cv2
import numpy as np
import tensorflow as tf
import torch
import matplotlib.pyplot as plt
from google.colab.patches import cv2_imshow

**IMPORTING PRETRAINED MODELS FOR TRAFFIC SIGNAL AND SIGN DETECTION**

In [ ]:
traffic_model = tf.keras.models.load_model('/content/drive/MyDrive/RGY_TRAFFIC_LIGHT_DET.h5')
# Load the YOLOv5 sign detection model (PyTorch)
model_path = '/content/drive/MyDrive/best.pt'
yolov5_model = torch.hub.load('ultralytics/yolov5:v7.0', 'custom', path=model_path)

Downloading: "https://github.com/ultralytics/yolov5/zipball/v7.0" to /root/.cache/torch/hub/v7.0.zip
YOLOv5 🚀 2024-11-8 Python-3.10.12 torch-2.5.0+cu121 CPU



requirements: /usr/local/lib/python3.10/dist-packages/requirements.txt not found, check failed.


Fusing layers... 
Model summary: 157 layers, 7026307 parameters, 0 gradients, 15.8 GFLOPs
Adding AutoShape... 


**IMPORTING PRETRAINED MODEL FOR OBJECT DETECTION**

In [ ]:
# Load the YOLOv5 pre-trained model (we'll use PyTorch to load YOLOv5)
model = torch.hub.load('ultralytics/yolov5', 'yolov5s')

/usr/local/lib/python3.10/dist-packages/torch/hub.py:330: UserWarning: You are about to download and run code from an untrusted repository. In a future release, this won't be allowed. To add the repository to your trusted list, change the command to {calling_fn}(..., trust_repo=False) and a command prompt will appear asking for an explicit confirmation of trust, or load(..., trust_repo=True), which will assume that the prompt is to be answered with 'yes'. You can also use load(..., trust_repo='check') which will only prompt for confirmation if the repo is not already trusted. This will eventually be the default behaviour
  warnings.warn(
Downloading: "https://github.com/ultralytics/yolov5/zipball/master" to /root/.cache/torch/hub/master.zip


Creating new Ultralytics Settings v0.0.6 file ✅ 
View Ultralytics Settings with 'yolo settings' or at '/root/.config/Ultralytics/settings.json'
Update Settings with 'yolo settings key=value', i.e. 'yolo settings runs_dir=path/to/dir'. For help see https://docs.ultralytics.com/quickstart/#ultralytics-settings.


YOLOv5 🚀 2024-11-8 Python-3.10.12 torch-2.5.0+cu121 CPU

100%|██████████| 14.1M/14.1M [00:00<00:00, 121MB/s]

Fusing layers... 
YOLOv5s summary: 213 layers, 7225885 parameters, 0 gradients, 16.4 GFLOPs
Adding AutoShape... 


**Traffic Light Signal Detection: Identifying Dominant Color (Red, Yellow, Green) through Masking and Brightness Analysis**

In [ ]:
def resize_image(rgb_image, size=(32, 32)):
    return cv2.resize(rgb_image, size)

def mask_image_get_brightness_vector(rgb_image):
    resized_image = resize_image(rgb_image, (32, 32))
    hsv = cv2.cvtColor(resized_image, cv2.COLOR_RGB2HSV)

    lower_red1 = np.array([0, 70, 50])
    upper_red1 = np.array([10, 255, 255])
    lower_red2 = np.array([170, 70, 50])
    upper_red2 = np.array([180, 255, 255])

    lower_yellow = np.array([20, 100, 100])
    upper_yellow = np.array([30, 255, 255])

    lower_green = np.array([40, 70, 50])
    upper_green = np.array([80, 255, 255])

    mask_red1 = cv2.inRange(hsv, lower_red1, upper_red1)
    mask_red2 = cv2.inRange(hsv, lower_red2, upper_red2)
    mask_red = cv2.bitwise_or(mask_red1, mask_red2)

    mask_yellow = cv2.inRange(hsv, lower_yellow, upper_yellow)
    mask_green = cv2.inRange(hsv, lower_green, upper_green)

    masked_red_image = cv2.bitwise_and(resized_image, resized_image, mask=mask_red)
    masked_yellow_image = cv2.bitwise_and(resized_image, resized_image, mask=mask_yellow)
    masked_green_image = cv2.bitwise_and(resized_image, resized_image, mask=mask_green)

    # Calculate brightness vector for each color
    red_brightness_sum = np.sum(masked_red_image[:, :, 0])  # Sum of red
    yellow_brightness_sum = np.sum(masked_yellow_image[:, :, 0])  # Sum of yellow
    green_brightness_sum = np.sum(masked_green_image[:, :, 0])  # Sum of green

    # Determine which color has the highest brightness
    color_brightness = {
        'Red': red_brightness_sum,
        'Yellow': yellow_brightness_sum,
        'Green': green_brightness_sum
    }

    max_color = max(color_brightness, key=color_brightness.get)
    return max_color, (resized_image, masked_red_image, masked_yellow_image, masked_green_image)


**Traffic Light Color Prediction: Classifying Green, Red, and Yellow Signals with Confidence Check With CNN Model.**

In [ ]:
import tensorflow as tf
import numpy as np

# Set a confidence threshold
CONFIDENCE_THRESHOLD = 0.3

def predict_object(frame, model):
    # Resize frame to match model's input dimensions
    resized_frame = cv2.resize(frame, (240, 240))
    frame_array = tf.keras.preprocessing.image.img_to_array(resized_frame)
    frame_array = np.expand_dims(frame_array, axis=0)  # Add batch dimension

    # Make prediction using the Keras model
    result = model.predict(frame_array)
    probabilities = tf.nn.softmax(result).numpy()

    # Get the predicted class and its confidence
    pred_class = np.argmax(probabilities, axis=1)[0]
    confidence = probabilities[0][pred_class]

    # Check if confidence meets threshold
    if confidence < CONFIDENCE_THRESHOLD:
        return "Cant determine"

    # Map prediction to traffic light colors
    if pred_class == 1:
        return "Green"
    elif pred_class == 2:
        return "Red"
    elif pred_class == 3:
        return "Yellow"
    else:
        return "Cant determine"


**Traffic Sign Recognition: Resizing Input Image Frame and Detecting Sign Class with YOLOv5 Model.**

In [ ]:
def resizes_image(image, target_width=640):
    height, width = image.shape[:2]
    print(height, width)
    width = int(width)
    height = int(height)
    scale = target_width / width
    print(scale)
    new_size = (target_width, int(height * scale))
    return cv2.resize(image, new_size)


def predict_sign(object_region ,yolov5_model):
    resized_image = resizes_image(object_region, 640)
    results = yolov5_model(resized_image)
    detections = results.xyxy[0].cpu().numpy()
    if len(detections) > 0:
        # Extract the label of the first detection
        class_id = int(detections[0][5])
        label = yolov5_model.names[class_id]
        return label
    return "No sign detected"

**VIDEO DETECTION**

In [ ]:
import os
import cv2

# Paths for input and output videos
video_path = '/content/drive/MyDrive/output5.mp4'  # Input video path
output_path = '/content/drive/MyDrive/output_video55.mp4'  # Output video path
# Set up output directory if it doesn't exist
output_dir = os.path.dirname(output_path)
if not os.path.exists(output_dir):
    os.makedirs(output_dir)


In [ ]:
# Open the input video
cap = cv2.VideoCapture(video_path)
frame_width = int(cap.get(cv2.CAP_PROP_FRAME_WIDTH))
frame_height = int(cap.get(cv2.CAP_PROP_FRAME_HEIGHT))
fps = int(cap.get(cv2.CAP_PROP_FPS))

In [ ]:
# Define codec and create VideoWriter for the output video
fourcc = cv2.VideoWriter_fourcc(*'mp4v')
out = cv2.VideoWriter(output_path, fourcc, fps, (frame_width, frame_height))

**VIDEO PROCESSING**

In [ ]:

while cap.isOpened():
    ret, frame = cap.read()
    if not ret:
        break

    # Perform YOLOv5 inference on the frame
    results = model(frame)
    detections = results.xyxy[0].cpu().numpy()

    for detection in detections:
        x1, y1, x2, y2, conf, class_id = detection[:6]
        object_region = frame[int(y1):int(y2), int(x1):int(x2)]

        cnn_detect = predict_object(object_region, traffic_model)
        brightness_label, (resized_image, masked_red_image, masked_yellow_image, masked_green_image) = mask_image_get_brightness_vector(object_region)

        if cnn_detect.lower() == brightness_label.lower():
            final_label = cnn_detect
        else:
            final_label = "Cant determine"

        if final_label == "Cant determine":
            new_label = predict_sign(object_region, yolov5_model)
            if new_label:
                final_label = new_label

        # Draw bounding box and label on the frame
        if final_label.lower() in ["green", "red", "yellow"]:
            color = (0, 255, 0) if final_label.lower() == "green" else (0, 0, 255) if final_label.lower() == "red" else (0, 255, 255)
            label_text = f"Traffic Light: {final_label.capitalize()}"
        else:
            color = (255, 165, 0)  # Orange for traffic sign
            label_text = f"Sign: {final_label.capitalize()}"

        # Draw rectangle and text for the detected object
        cv2.rectangle(frame, (int(x1), int(y1)), (int(x2), int(y2)), color, 2)
        cv2.putText(frame, label_text, (int(x1), int(y1) - 10), cv2.FONT_HERSHEY_SIMPLEX, 0.9, color, 2)

    # Write the processed frame to the output video
    out.write(frame)

# Release resources
cap.release()
out.release()
cv2.destroyAllWindows()

print("Video processing completed. Output saved at:", output_path)

/root/.cache/torch/hub/ultralytics_yolov5_master/models/common.py:892: FutureWarning: `torch.cuda.amp.autocast(args...)` is deprecated. Please use `torch.amp.autocast('cuda', args...)` instead.
  with amp.autocast(autocast):


1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 423ms/step
253 133
4.81203007518797


/root/.cache/torch/hub/ultralytics_yolov5_master/models/common.py:892: FutureWarning: `torch.cuda.amp.autocast(args...)` is deprecated. Please use `torch.amp.autocast('cuda', args...)` instead.
  with amp.autocast(autocast):


1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 117ms/step
182 67
9.552238805970148


/root/.cache/torch/hub/ultralytics_yolov5_master/models/common.py:892: FutureWarning: `torch.cuda.amp.autocast(args...)` is deprecated. Please use `torch.amp.autocast('cuda', args...)` instead.
  with amp.autocast(autocast):


...

1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 145ms/step
52 26
24.615384615384617


/root/.cache/torch/hub/ultralytics_yolov5_master/models/common.py:892: FutureWarning: `torch.cuda.amp.autocast(args...)` is deprecated. Please use `torch.amp.autocast('cuda', args...)` instead.
  with amp.autocast(autocast):


1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 151ms/step
70 65
9.846153846153847


/root/.cache/torch/hub/ultralytics_yolov5_master/models/common.py:892: FutureWarning: `torch.cuda.amp.autocast(args...)` is deprecated. Please use `torch.amp.autocast('cuda', args...)` instead.
  with amp.autocast(autocast):


1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 161ms/step


**PROCESSED VIDEOS LINK:**

https://drive.google.com/drive/folders/1nsuITzVwcD_ZGwYVuupE9RR53whl7_rB?usp=sharing

